In [1]:
from bs4 import BeautifulSoup
import os
import pandas
from datetime import datetime, timedelta
from elasticsearch import Elasticsearch
from elasticsearch_dsl import Search
from tqdm import tqdm
import requests
import json
from tika import parser
import re
from unidecode import unidecode
from tqdm import tqdm
from glob import glob
import json
import openai
import time

In [6]:
TIKA_HOST = os.environ.get('TIKA_HOST', 'http://localhost:9998')

directory = 'pdf_temp'
index = 'hansard'

def cleaning(string):
    string = unidecode(string).replace('\t', ' ').replace('\r', ' ').replace('\n', ' ').replace('_', ' ')
    string = string.replace(' -', '-').replace(' ANYA', 'ANYA').replace('ki ta', 'kita').replace('s aya', 'saya')
    string = string.replace('m enjadi', 'menjadi').replace('meno lak', 'menolak')
    try:
        soup = BeautifulSoup(string, 'lxml')
        string = soup.text
    except:
        pass
    return re.sub(r'[ ]+', ' ', string).strip()

def download(url, file_name):
    with open(file_name, "wb") as file:
        response = requests.get(url)
        file.write(response.content)

os.makedirs(directory, exist_ok = True)
latest_date = datetime.strptime('2024-01-01', '%Y-%m-%d')

startDate = latest_date
endDate = latest_date + timedelta(days=30 * 8)
datesRange = pandas.date_range(startDate,endDate-timedelta(days=1),freq='d')
datesRange = [d.strftime('%d%m%Y') for d in datesRange]

['01012024', '02012024', '03012024', '04012024', '05012024', '06012024', '07012024', '08012024', '09012024', '10012024', '11012024', '12012024', '13012024', '14012024', '15012024', '16012024', '17012024', '18012024', '19012024', '20012024', '21012024', '22012024', '23012024', '24012024', '25012024', '26012024', '27012024', '28012024', '29012024', '30012024', '31012024', '01022024', '02022024', '03022024', '04022024', '05022024', '06022024', '07022024', '08022024', '09022024', '10022024', '11022024', '12022024', '13022024', '14022024', '15022024', '16022024', '17022024', '18022024', '19022024', '20022024', '21022024', '22022024', '23022024', '24022024', '25022024', '26022024', '27022024', '28022024', '29022024', '01032024', '02032024', '03032024', '04032024', '05032024', '06032024', '07032024', '08032024', '09032024', '10032024', '11032024', '12032024', '13032024', '14032024', '15032024', '16032024', '17032024', '18032024', '19032024', '20032024', '21032024', '22032024', '23032024', '24

In [4]:
for d in tqdm(datesRange):
    filename = f'DR-{d}.pdf'
    output_filename = os.path.join(directory, filename)
    if os.path.exists(output_filename) and os.path.getsize(output_filename) > 1000:
        print(f'{output_filename} exists, skip.')
        continue
    url = f'https://www.parlimen.gov.my/files/hindex/pdf/{filename}'
    try:
        download(url, output_filename)
    except Exception as e:
        print(e)

100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████| 240/240 [00:47<00:00,  5.05it/s]


In [8]:
pdfs = sorted(glob(f'{directory}/*.pdf'))
print(pdfs)

print('writing hansard-temp.jsonl')
with open('hansard-temp.jsonl', 'w') as fopen:
    for file in tqdm(pdfs):

        raw_xml = parser.from_file(file, f'{TIKA_HOST}/tika', xmlContent=True)
        body = raw_xml['content'].split('<body>')[1].split('</body>')[0]
        body_without_tag = body.replace("<p>", "").replace("</p>", "").replace("<div>", "").replace("</div>","").replace("<p />","")
        text_pages = body_without_tag.split("""<div class="page">""")[1:]

        for i, t in enumerate(text_pages):
            r = re.findall(r'DR[\. ]\s*[0-3]?[0-9].[0-3]?[0-9].(?:[0-9]{2})?[0-9]{2}\s+\d+\b', t)
            r_ = re.findall(r'\d+\s+DR[\. ]\s*[0-3]?[0-9].[0-3]?[0-9].(?:[0-9]{2})?[0-9]{2}\b', t)
            found = True
            if len(r):
                no_page = r[0].split()[-1]
            elif len(r_):
                no_page = r_[0].split()[0]
            else:
                found = False

            if not found:
                continue

            splitted = t.split('\n \n')
            splitted = [s for s in splitted if len(s.strip()) > 1]
            if len(splitted) < 3:
                splitted = t.split('\n\n')
            splitted = [cleaning(s) for s in splitted[1:]]
            splitted = [s + '.' if s[-1] not in  '.;:,' else s for s in splitted if len(s)]
            splitted = ' '.join(splitted)
            date = datetime.strptime(file, f'{directory}/DR-%d%m%Y.pdf').strftime('%Y-%m-%d')
            
            if not len(splitted):
                print(f, i, t)

            d = {
                'original': t,
                'cleaned': splitted,
                'no_page': int(no_page),
                'actual_no_page': i + 1,
                'date': date,
                'url': f'https://www.parlimen.gov.my/files/hindex/{file}'.replace('/pdf_temp', '/pdf')
            }
            fopen.write(f'{json.dumps(d)}\n')